In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt


import nltk
nltk.download('omw-1.4')
nltk.download("punkt")
nltk.download("wordnet")
nltk.download("stopwords")

from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing import sequence 

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, SimpleRNN, Dropout, Embedding
import warnings
warnings.filterwarnings("ignore")

[nltk_data] Downloading package omw-1.4 to C:\Users\MY
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package punkt to C:\Users\MY
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to C:\Users\MY
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to C:\Users\MY
[nltk_data]     PC\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
df=pd.read_csv("fake_job_postings.csv")

In [3]:
df.head()

job_id                                      title            location  \
0       1                           Marketing Intern    US, NY, New York   
1       2  Customer Service - Cloud Video Production      NZ, , Auckland   
2       3    Commissioning Machinery Assistant (CMA)       US, IA, Wever   
3       4          Account Executive - Washington DC  US, DC, Washington   
4       5                        Bill Review Manager  US, FL, Fort Worth   

  department salary_range                                    company_profile  \
0  Marketing          NaN  We're Food52, and we've created a groundbreaki...   
1    Success          NaN  90 Seconds, the worlds Cloud Video Production ...   
2        NaN          NaN  Valor Services provides Workforce Solutions th...   
3      Sales          NaN  Our passion for improving quality of life thro...   
4        NaN          NaN  SpotSource Solutions LLC is a Global Human Cap...   

                                         description  \
0  Food52, a fast-growing, James Beard Award-winn...   
1  Organised - Focused - Vibrant - Awesome!Do you...   
2  Our client, located in Houston, is actively se...   
3  THE COMPANY: ESRI – Environmental Systems Rese...   
4  JOB TITLE: Itemization Review ManagerLOCATION:...   

                                        requirements  \
0  Experience with content management systems a m...   
1  What we expect from you:Your key responsibilit...   
2  Implement pre-commissioning and commissioning ...   
3  EDUCATION: Bachelor’s or Master’s in GIS, busi...   
4  QUALIFICATIONS:RN license in the State of Texa...   

                                            benefits  telecommuting  \
0                                                NaN              0   
1  What you will get from usThrough being part of...              0   
2                                                NaN              0   
3  Our culture is anything but corporate—we have ...              0   
4                              Full Benefits Offered              0   

   has_company_logo  has_questions employment_type required_experience  \
0                 1              0           Other          Internship   
1                 1              0       Full-time      Not Applicable   
2                 1              0             NaN                 NaN   
3                 1              0       Full-time    Mid-Senior level   
4                 1              1       Full-time    Mid-Senior level   

  required_education                   industry              function  \
0                NaN                        NaN             Marketing   
1                NaN  Marketing and Advertising      Customer Service   
2                NaN                        NaN                   NaN   
3  Bachelor's Degree          Computer Software                 Sales   
4  Bachelor's Degree     Hospital & Health Care  Health Care Provider   

   fraudulent  
0           0  
1           0  
2           0  
3           0  
4           0

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17880 entries, 0 to 17879
Data columns (total 18 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   job_id               17880 non-null  int64 
 1   title                17880 non-null  object
 2   location             17534 non-null  object
 3   department           6333 non-null   object
 4   salary_range         2868 non-null   object
 5   company_profile      14572 non-null  object
 6   description          17879 non-null  object
 7   requirements         15185 non-null  object
 8   benefits             10670 non-null  object
 9   telecommuting        17880 non-null  int64 
 10  has_company_logo     17880 non-null  int64 
 11  has_questions        17880 non-null  int64 
 12  employment_type      14409 non-null  object
 13  required_experience  10830 non-null  object
 14  required_education   9775 non-null   object
 15  industry             12977 non-null  object
 16  func

In [5]:
df.describe()

job_id  telecommuting  has_company_logo  has_questions  \
count  17880.000000   17880.000000      17880.000000   17880.000000   
mean    8940.500000       0.042897          0.795302       0.491723   
std     5161.655742       0.202631          0.403492       0.499945   
min        1.000000       0.000000          0.000000       0.000000   
25%     4470.750000       0.000000          1.000000       0.000000   
50%     8940.500000       0.000000          1.000000       0.000000   
75%    13410.250000       0.000000          1.000000       1.000000   
max    17880.000000       1.000000          1.000000       1.000000   

         fraudulent  
count  17880.000000  
mean       0.048434  
std        0.214688  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        0.000000  
max        1.000000

In [6]:
df.isnull().sum()

job_id                     0
title                      0
location                 346
department             11547
salary_range           15012
company_profile         3308
description                1
requirements            2695
benefits                7210
telecommuting              0
has_company_logo           0
has_questions              0
employment_type         3471
required_experience     7050
required_education      8105
industry                4903
function                6455
fraudulent                 0
dtype: int64

In [7]:
 #romoving a nan value
columns=['job_id', 'telecommuting', 'has_company_logo', 'has_questions', 'salary_range', 'employment_type']
for col in columns:
    del df[col]

df.fillna(' ', inplace=True)

In [8]:
df['job_details']=df['title']+' '+df['location']+' '+df['company_profile']+' '+df['description']+' '+df['requirements']+' '+df['benefits']

In [9]:
columns1=["title","location","company_profile","description","requirements","benefits","industry","required_education","department","function","required_experience"]
for col1 in columns1:
    del df[col1]

In [10]:
df.head()

fraudulent                                        job_details
0           0  Marketing Intern US, NY, New York We're Food52...
1           0  Customer Service - Cloud Video Production NZ, ...
2           0  Commissioning Machinery Assistant (CMA) US, IA...
3           0  Account Executive - Washington DC US, DC, Wash...
4           0  Bill Review Manager US, FL, Fort Worth SpotSou...

In [11]:
df["fraudulent"].value_counts()

0    17014
1      866
Name: fraudulent, dtype: int64

In [12]:
def cleantext(job_details):
  tokens = word_tokenize(job_details.lower())
  ftoken = [t for t in tokens if(t.isalpha())]
  stop = stopwords.words("english")
  ctoken = [t for t in ftoken if(t not in stop)]
  lemma = WordNetLemmatizer()
  ltoken = [lemma.lemmatize(t) for t in ctoken]
  return " ".join(ltoken)

In [13]:
df["clean_job_details"]=df["job_details"].apply(cleantext)

In [14]:
df.head()

fraudulent                                        job_details  \
0           0  Marketing Intern US, NY, New York We're Food52...   
1           0  Customer Service - Cloud Video Production NZ, ...   
2           0  Commissioning Machinery Assistant (CMA) US, IA...   
3           0  Account Executive - Washington DC US, DC, Wash...   
4           0  Bill Review Manager US, FL, Fort Worth SpotSou...   

                                   clean_job_details  
0  marketing intern u ny new york created groundb...  
1  customer service cloud video production nz auc...  
2  commissioning machinery assistant cma u ia wev...  
3  account executive washington dc u dc washingto...  
4  bill review manager u fl fort worth spotsource...

In [15]:
x = df["clean_job_details"]
y = df["fraudulent"]

In [16]:
xtrain, xtest, ytrain, ytest = train_test_split(x, y, test_size=0.3, random_state=1)

In [17]:
sentlen = []

for sent in df["clean_job_details"]:
  sentlen.append(len(word_tokenize(sent)))

df["SentLen"] = sentlen 
df.head()

fraudulent                                        job_details  \
0           0  Marketing Intern US, NY, New York We're Food52...   
1           0  Customer Service - Cloud Video Production NZ, ...   
2           0  Commissioning Machinery Assistant (CMA) US, IA...   
3           0  Account Executive - Washington DC US, DC, Wash...   
4           0  Bill Review Manager US, FL, Fort Worth SpotSou...   

                                   clean_job_details  SentLen  
0  marketing intern u ny new york created groundb...      225  
1  customer service cloud video production nz auc...      508  
2  commissioning machinery assistant cma u ia wev...      198  
3  account executive washington dc u dc washingto...      465  
4  bill review manager u fl fort worth spotsource...      334

In [18]:
max(sentlen)

1327

In [19]:
max_len=np.quantile(sentlen, 0.95)

In [20]:
tok = Tokenizer(char_level=False, split=" ")

In [21]:
tok.fit_on_texts(xtrain)
tok.index_word

{1: 'experience',
 2: 'work',
 3: 'team',
 4: 'service',
 5: 'company',
 6: 'customer',
 7: 'business',
 8: 'u',
 9: 'client',
 10: 'product',
 11: 'new',
 12: 'year',
 13: 'skill',
 14: 'amp',
 15: 'management',
 16: 'development',
 17: 'sale',
 18: 'working',
 19: 'project',
 20: 'job',
 21: 'technology',
 22: 'opportunity',
 23: 'design',
 24: 'people',
 25: 'solution',
 26: 'marketing',
 27: 'communication',
 28: 'time',
 29: 'looking',
 30: 'position',
 31: 'ability',
 32: 'process',
 33: 'help',
 34: 'support',
 35: 'data',
 36: 'software',
 37: 'including',
 38: 'candidate',
 39: 'environment',
 40: 'knowledge',
 41: 'office',
 42: 'need',
 43: 'web',
 44: 'manager',
 45: 'system',
 46: 'professional',
 47: 'provide',
 48: 'application',
 49: 'employee',
 50: 'quality',
 51: 'one',
 52: 'industry',
 53: 'required',
 54: 'well',
 55: 'world',
 56: 'best',
 57: 'medium',
 58: 'strong',
 59: 'role',
 60: 'offer',
 61: 'make',
 62: 'also',
 63: 'high',
 64: 'technical',
 65: 'based'

In [22]:
vocab_len = len(tok.index_word)
vocab_len

73897

In [23]:
seqtrain = tok.texts_to_sequences(xtrain) #step1
seqtrain

[[1567,
  5377,
  555,
  389,
  446,
  3235,
  8,
  1116,
  8142,
  271,
  209,
  8142,
  2835,
  759,
  105,
  389,
  360,
  5377,
  833,
  86,
  795,
  1567,
  360,
  23908,
  795,
  23909,
  795,
  1567,
  360,
  23910,
  795,
  370,
  214,
  140,
  30,
  759,
  952,
  3236,
  404,
  88,
  795,
  23911,
  2,
  23912,
  269,
  360,
  5377,
  180,
  360,
  105,
  23913,
  269,
  370,
  23914,
  1045],
 [10,
  44,
  8,
  499,
  11,
  331,
  4743,
  122,
  91,
  1280,
  15,
  727,
  4743,
  1108,
  722,
  784,
  963,
  4265,
  617,
  5011,
  487,
  557,
  727,
  134,
  1182,
  1942,
  149,
  600,
  185,
  49,
  364,
  5012,
  11,
  331,
  313,
  41,
  393,
  231,
  1662,
  24,
  786,
  761,
  396,
  1427,
  252,
  963,
  12850,
  2693,
  1496,
  787,
  4200,
  5,
  776,
  140,
  2076,
  11161,
  83,
  273,
  2383,
  155,
  56,
  1,
  79,
  415,
  61,
  2325,
  1624,
  9026,
  9027,
  673,
  56,
  7,
  2121,
  2826,
  9026,
  9027,
  673,
  56,
  821,
  25,
  4743,
  62,
  479,
  539,
  

In [24]:
seqmattrain = sequence.pad_sequences(seqtrain, maxlen= int(max_len)) #step2
seqmattrain

array([[    0,     0,     0, ...,   370, 23914,  1045],
       [    0,     0,     0, ...,    58,   340,   296],
       [    0,     0,     0, ...,   662,  3028,   932],
       ...,
       [    0,     0,     0, ...,   258,   693,   374],
       [    0,     0,     0, ...,   396,   471,   590],
       [    0,     0,     0, ...,   629,   317,   690]])

In [25]:
seqtest = tok.texts_to_sequences(xtest)
seqmattest = sequence.pad_sequences(seqtest, maxlen=int(max_len))

In [26]:
rnn = Sequential()

rnn.add(Embedding(vocab_len+1,700, input_length=int(max_len), mask_zero=True))
rnn.add(SimpleRNN(units=32, activation="tanh"))
rnn.add(Dense(units=32, activation="relu"))
rnn.add(Dropout(0.2))

rnn.add(Dense(units=1, activation="sigmoid"))

rnn.compile(optimizer="adam", loss="binary_crossentropy")

rnn.fit(seqmattrain, ytrain, batch_size=50, epochs=25)

ypred = rnn.predict(seqmattest)

ypred = np.where(ypred>0.5,1,0)

Epoch 1/25
251/251 [==============================] - 233s 910ms/step - loss: 0.1792
Epoch 2/25
251/251 [==============================] - 243s 967ms/step - loss: 0.0466
Epoch 3/25
251/251 [==============================] - 268s 1s/step - loss: 0.0111
Epoch 4/25
251/251 [==============================] - 257s 1s/step - loss: 0.0051
Epoch 5/25
251/251 [==============================] - 246s 981ms/step - loss: 0.0043
Epoch 6/25
251/251 [==============================] - 245s 975ms/step - loss: 0.0024
Epoch 7/25
251/251 [==============================] - 243s 969ms/step - loss: 0.0025
Epoch 8/25
251/251 [==============================] - 243s 966ms/step - loss: 0.0020
Epoch 9/25
251/251 [==============================] - 242s 962ms/step - loss: 0.0021
Epoch 10/25
251/251 [==============================] - 258s 1s/step - loss: 0.0017
Epoch 11/25
251/251 [==============================] - 268s 1s/step - loss: 0.0014
Epoch 12/25
251/251 [==============================] - 245s 978ms/step - lo

In [27]:
ypred

array([[0],
       [0],
       [0],
       ...,
       [0],
       [0],
       [0]])

In [28]:
from sklearn.metrics import classification_report

In [29]:
print(classification_report(ytest,ypred))

              precision    recall  f1-score   support

           0       0.98      0.98      0.98      5143
           1       0.62      0.61      0.61       221

    accuracy                           0.97      5364
   macro avg       0.80      0.80      0.80      5364
weighted avg       0.97      0.97      0.97      5364

